# Тематическое моделирование

Задача тематического моделирования состоит в том, чтобы разложить слова, употребляющиеся в корпусе на темы и приписать эти темы каждому документу в корпусе.

Помимо анализа тематического наполнения корпуса, тематическое моделирование может использоваться для:

1) построения вектроных представлений текстов (числа показывают насколько тема выражена в тексте). Такие представления могут быть лучше обычных (TfidfVectorizer, CountVectorizer), т.к. позволяют находить близкие документы даже если в них нет одинаковых слов (но есть слова одной тематики). Тематические векторы могут использоваться для поиска, рекомендаций или как признаки в классификации. 

2) приписывания тэгов текстам. Так можно автоматически выделять в текстовых потоках тренды, горячие темы. Тэги можно использовать как фильтр в поисковых системах. Тэги нужно приписывать темам вручную, но это проще чем размечать обучающую выборку, так как слова в тематике сразу подказывают название. 

3) составления тематических словарей



Кроме обычных текстов тематическое моделирование применяется к многим другим данным: запросам пользователей, сайтам, на которые заходят пользователи, музыке, которую слушают пользователи, покупкам в одной корзине, банковским транзакциям и даже днк. 


Все подходы к тематическому моделированию так или иначе основнованы на:

1) модели мешка слов (т.е. порядок слов в документах не учитывается)  
2) независимости документов между собой  (т.е. употребление слова W в тексте D_1 никак не влияет на слова в документе D_2)  
3) дистрибутивной гипотезе (слова, употребляющиеся вместе, объединяются в темы)



В этой тетрадке для получения тематических моделей используются LDA из gensim и NMF из sklearn.

Про LDA (и в целом тематическое моделирование) можно почитать вот эту статью - https://sysblok.ru/knowhow/kak-ponjat-o-chem-tekst-ne-chitaja-ego/

In [1]:
import gensim
import json
import re
import pandas as pd
from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords
from pymorphy2 import MorphAnalyzer
import pyLDAvis.gensim
import string
from collections import Counter
import warnings
warnings.filterwarnings("ignore")
from IPython.display import Image
from IPython.core.display import HTML 
morph = MorphAnalyzer()

## Данные

Возьмем 10 тыс статьи с Википедии. 

Токенизируем самым простым способом и нормализуем Pymorphy.

In [2]:
stops = set(stopwords.words('russian'))

# чтобы быстрее нормализовать тексты, создадим словарь всех словоформ
# нормазуем каждую 1 раз и положим в словарь
# затем пройдем по текстам и сопоставим каждой словоформе её нормальную форму

def opt_normalize(texts, top=None):
    uniq = Counter()
    for text in texts:
        uniq.update(text)
    
    norm_uniq = {word:morph.parse(word)[0].normal_form for word, _ in uniq.most_common(top)}
    
    norm_texts = []
    for text in texts:
        
        norm_words = [norm_uniq.get(word) for word in text]
        norm_words = [word for word in norm_words if word and word not in stops]
        norm_texts.append(norm_words)
        
    return norm_texts

def tokenize(text):
    words = [word.strip(string.punctuation) for word in text.split()]
    words = [word for word in words if word]
    
    return words

In [3]:
texts = open('wiki_data.txt').read().splitlines()[:10000]

In [4]:
len(texts)

10000

In [5]:
texts = opt_normalize([tokenize(text.lower()) for text in texts], 30000)

In [6]:
texts[:3]

[['нижегородский',
  '—',
  'сельский',
  'посёлок',
  'район',
  'нижегородский',
  'область',
  'входить',
  'состав',
  'расположить',
  '12,5',
  'километр',
  'юг',
  'село',
  '1',
  'километр',
  'запасть',
  'город',
  'право',
  'берег',
  'река',
  'правый',
  'приток',
  'река',
  'сатис',
  'окружить',
  'смешанный',
  'леса',
  'соединить',
  'дорогой',
  'посёлок',
  '1,5',
  'километр',
  'дорога',
  'посёлок',
  'сатис',
  '3,5',
  'километр',
  'название',
  'являться',
  'сугубо',
  'официальный',
  'местный',
  'население',
  'использовать',
  'исключительно',
  'название',
  '—',
  'употребляться',
  'языковой',
  'оборот',
  'ранее',
  'использовать',
  'название',
  '—',
  '1920-ха',
  'год',
  'переселенец',
  'соседний',
  'село',
  'аламасовый',
  'расположить',
  'соответственно',
  '8',
  '14',
  'километр',
  'запасть',
  'посёлок',
  'жить',
  'рабочий',
  'совхоз',
  'центр',
  'посёлок',
  'сатис',
  'возле',
  'посёлок',
  'расположить',
  'активно',
  '

In [7]:
# для нграммов
# ph = gensim.models.Phrases(texts, scoring='npmi', threshold=0.4) # threshold можно подбирать
# p = gensim.models.phrases.Phraser(ph)
# ngrammed_texts = p[texts]

### Тематическое моделирование в gensim

Для моделей нужно сделать словарь.

In [8]:
dictinary = gensim.corpora.Dictionary(texts)

In [9]:
dictinary.filter_extremes(no_above=0.1, no_below=10)
dictinary.compactify()

In [10]:
print(dictinary)

Dictionary(8711 unique tokens: ['1,2', '1,5', '12', '12,5', '14']...)


Преобразуем наши тексты в мешки слов. 

In [11]:
corpus = [dictinary.doc2bow(text) for text in texts]

Про параметры можно почитать в документации:

In [12]:
?gensim.models.LdaMulticore

Основные это num_topics, alpha, eta и passes. 

**num_topics** - это количество тем. Это основной параметр и настраивать его проще всего. Обычно 200 оптимальное значение. Можно поставить поменьше, если тексты не очень разнообразные или хочется уменьшить время обучения.

**alpha** и **eta** - параметры, которые влияют на разреженность распределения документы-темы и темы-слова. У alpha есть значения "asymmetric" и "auto", которые можно попробовать (по умолчанию стоит "symmetric", т.е. не разреженное). Eta можно задать каким-то числом или самому сделать изначальное распределение слов по темам. НО настраивать эти параметры сложно и непонятно и вообще лучше надеяться, что по умолчанию все заработает.

**passes** - задает количество проходов по данным. Чем больше, тем лучше сойдется модель, но обучаться будет дольше.

In [13]:
lda = gensim.models.LdaMulticore(corpus, 100, id2word=dictinary, passes=10) # если поддерживается многопоточность
# lda = gensim.models.LdaModel(200, id2word=dictinary, passes=5)

Посмотрим на топики.

In [175]:
lda.print_topics()

[(5,
  '0.015*"сын" + 0.015*"брак" + 0.015*"де" + 0.009*"дочь" + 0.009*"французский" + 0.008*"отец" + 0.008*"смерть" + 0.007*"ii" + 0.007*"вместе" + 0.007*"мария"'),
 (44,
  '0.033*"народичский" + 0.024*"ложа" + 0.015*"4140" + 0.014*"великое" + 0.013*"больница" + 0.013*"тверская" + 0.011*"области.############код" + 0.010*"великий" + 0.009*"знак" + 0.009*"медицинский"'),
 (20,
  '0.028*"игрок" + 0.010*"игровой" + 0.010*"уровень" + 0.009*"the" + 0.008*"каждый" + 0.008*"соревнование" + 0.006*"playstation" + 0.006*"компания" + 0.006*"выпустить" + 0.006*"комплекс"'),
 (65,
  '0.069*"улица" + 0.027*"станция" + 0.027*"дом" + 0.016*"линия" + 0.013*"москва" + 0.009*"построить" + 0.008*"век" + 0.008*"сторона" + 0.008*"проходить" + 0.007*"строительство"'),
 (97,
  '0.027*"герб" + 0.016*"тысяча" + 0.016*"щит" + 0.011*"луи" + 0.008*"осетия" + 0.007*"южный" + 0.006*"пол" + 0.005*"данные" + 0.005*"золотой" + 0.005*"текст"'),
 (19,
  '0.025*"windows" + 0.022*"турнир" + 0.020*"снукер" + 0.018*"ружински

Ещё есть штука для визуализации.

In [14]:
pyLDAvis.enable_notebook()

In [15]:
pyLDAvis.gensim.prepare(lda, corpus, dictinary)

PreparedData(topic_coordinates=              x         y  topics  cluster      Freq
topic                                               
70     0.049419 -0.019762       1        1  4.196151
76    -0.127808  0.079057       2        1  4.070893
61     0.155516  0.048011       3        1  3.274316
69     0.211810 -0.063771       4        1  2.914061
36     0.106048  0.209783       5        1  2.777511
...         ...       ...     ...      ...       ...
11    -0.057193 -0.012933      96        1  0.216636
23     0.055557 -0.058223      97        1  0.199183
48     0.023976  0.038330      98        1  0.170054
82     0.006662  0.054236      99        1  0.154525
1      0.018258 -0.017103     100        1  0.127463

[100 rows x 5 columns], topic_info=           Term         Freq        Total  Category  logprob  loglift
606        уезд  1793.000000  1793.000000   Default  30.0000  30.0000
2878     летний  1387.000000  1387.000000   Default  29.0000  29.0000
1253  завоевать  1080.000000  1080.000000   Default  28.0000  28.0000
1263       матч  1352.000000  1352.000000   Default  27.0000  27.0000
59         река  1807.000000  1807.000000   Default  26.0000  26.0000
...         ...          ...          ...       ...      ...      ...
1099        род     4.332854  1342.942871  Topic100  -5.7079   0.9287
11           24     3.936699   520.236328  Topic100  -5.8038   1.7812
1708  советский     4.211645  1619.759155  Topic100  -5.7363   0.7129
481         the     3.917120   838.399048  Topic100  -5.8088   1.2990
379           4     3.911788  1274.596680  Topic100  -5.8102   0.8787

[5862 rows x 6 columns], token_table=      Topic      Freq     Term
term                          
8612     12  0.195323      0,7
8612     19  0.130215      0,7
8612     20  0.065108      0,7
8612     33  0.065108      0,7
8612     44  0.455754      0,7
...     ...       ...      ...
459      91  0.007055        №
459      92  0.001008        №
459      93  0.004032        №
459      94  0.001008        №
8183     27  0.861658  №48-зко

[76206 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[71, 77, 62, 70, 37, 74, 25, 51, 11, 59, 52, 40, 31, 6, 100, 78, 68, 60, 41, 55, 30, 3, 26, 5, 17, 33, 15, 63, 18, 89, 13, 9, 57, 76, 42, 99, 79, 65, 81, 54, 44, 8, 48, 87, 80, 39, 7, 21, 66, 34, 10, 97, 73, 45, 88, 98, 72, 91, 86, 64, 69, 28, 96, 50, 93, 32, 46, 56, 19, 36, 94, 1, 82, 29, 47, 16, 23, 58, 27, 35, 22, 85, 67, 92, 84, 20, 14, 4, 90, 38, 61, 53, 75, 43, 95, 12, 24, 49, 83, 2])

На графике должно быть как можно меньше пересекающихся кружков (т.е. темы состоят из разных слов), а сами кружки не должны быть огромными (скорее всего такую тему можно разбить на несколько поменьше).

Можно посмотреть метрики.

In [16]:
import numpy as np

Перплексия показывает насколько хороше моделируется корпус. Чем ближе к нулю, тем лучше. Можно использовать, чтобы настраивать количество проходов по корпусу (когда перестало улучшаться, то можно останавливаться).

In [17]:
lda.log_perplexity(corpus[:1000])

-15.434950414851821

Ещё есть когерентность. Она численно оценивает качество тем (проверяется, что темы состоят из разных слов и что в теме есть топ тематических слов). 

In [18]:
coherence_model_lda = gensim.models.CoherenceModel(model=lda, 
                                                  texts=texts, 
                                                   dictionary=dictinary, coherence='c_v')

Чем выше, тем лучше.

In [19]:
topics = []
for topic_id, topic in lda.show_topics(num_topics=100, formatted=False):
    topic = [word for word, _ in topic]
    topics.append(topic)

In [20]:
coherence_model_lda = gensim.models.CoherenceModel(topics=topics, 
                                                   texts=texts, 
                                                   dictionary=dictinary, coherence='c_v')

In [21]:
coherence_model_lda.get_coherence()

0.5389902685385823

Но все эти числа вспомогательны! Главные критерии качества модели: интерпретируемость и понятность тем (т.е. нужно глазами смотреть на каждую тему), а также польза для практической задачи, которую вы пытаетесь решить.

### Разложение матриц в sklearn

In [22]:
Image(url="https://www.researchgate.net/profile/Andrea_Bertozzi/publication/312157184/figure/fig1/AS:448453387001860@1483931027472/Conceptual-illustration-of-non-negative-matrix-factorization-NMF-decomposition-of-a.png",
     width=800, height=500)


NMF - превращает одну матрицу Words * Documents в произведение двух матриц Words * Topics и Topics * Documents (произведение не точно равно изначальной матрице, но достаточно близко - чем больше Topics, тем точнее, но больше тратиться памяти и времени). 

Таким образом, взяв одну из получившихся матриц, мы получим или тематические представления документов (вторая матрица - документы на темы), либо слова, разложенные по темам (первая матрица - темы на слова).

Отличие от LDA в том, что числа в матрицах не будут вероятностями, а просто каким-то положительными числам. Чем больше, тем сильнее слово или документ связан с темой. 

(Почему и как это все работает, вы можете почитать отдельно. Для практических задач хватит умения запускать все в sklearn) 

In [23]:
from sklearn.decomposition import NMF
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer
import pandas as pd

Sklearn принимает на вход строки, поэтому склеим наши списки.

In [24]:
stexts = [' '.join(text) for text in texts]

Сделаем матрицу слова-документы с помощью TfidfVectorizer

In [25]:
vectorizer = TfidfVectorizer(max_features=2000, min_df=10, max_df=0.1, ngram_range=(1,2))
X = vectorizer.fit_transform(stexts)

Разложим её.

In [26]:
# n_components - главный параметр в NMF, это количество тем. 
# Если данных много, то увеличения этого параметра сильно увеличивает время обучения
model = NMF(n_components=100)

In [27]:
model.fit(X)

NMF(alpha=0.0, beta_loss='frobenius', init=None, l1_ratio=0.0, max_iter=200,
  n_components=100, random_state=None, shuffle=False, solver='cd',
  tol=0.0001, verbose=0)

In [28]:
model.components_.shape # матрица темы на слова

(100, 2000)

In [29]:
model.transform(X).shape # матрица документы на темы

(10000, 100)

In [30]:
pd.set_option('display.max_columns', 100)
pd.set_option('display.max_rows', 100)

Вытащим словарь, по которому мы построили модель.

In [31]:
feat_names = vectorizer.get_feature_names()

Теперь посмотрим на матрицу темы-слова, отсортируем её по строкам и возьмем топ N слов, сопоставив индексы со словарём

In [32]:
top_words = model.components_.argsort()[:,:-5:-1]

for i in range(top_words.shape[0]):
    words = [feat_names[j] for j in top_words[i]]
    print(i, "--".join(words))

0 летний олимпийский--летний--олимпийский игра--участие летний
1 украина основать--год находиться--области код--составлять человек
2 век--xix--xix век--xx
3 расстояние километр--харьковский--расстояние--километр расположить
4 зимний олимпийский--зимний--олимпийский игра--участие зимний
5 украина находиться--области код--составлять человек--ул
6 новоград--новоград волынский--волынский--области население
7 клуб--матч--лига--забить
8 хутор--ростовский--район ростовский--ростовский области
9 ул--наш ул--карл--области население
10 род--подсемейство--около--некоторый
11 сын--отец--жена--ребёнок
12 овручский--области код--сергей--13
13 остров--относиться--километр--пролив
14 емильчинский--области код--украина находиться--23
15 населить пункт--населить--пункт--государство
16 уезд--год уезд--специальный район--округ
17 хорошевский--области население--украина находиться--украина основать
18 альбом--the--of--выпустить
19 коростенский--области код--украина основать--год находиться
20 фильм--режисс

У разложения есть метрика, показывающая насколько хорошо восстанавливается изначальная матрица. Чем меньше, тем лучше.

In [33]:
model.reconstruction_err_

75.55903205047089

Но как и с LDA - главное это польза от модели и человеческая оценка, получаемых тем.

## Домашнее задание

Основаная задача - **построить хорошую тематическую модель с интерпретируемыми топиками с помощью LDA в gensim и NMF в sklearn**.


1) сделайте нормализацию (если pymorphy2 работает долго используйте mystem или попробуйте установить быструю версию - `pip install pymorphy2[fast]`, можно использовать какой-то другой токенизатор); 

2) добавьте нграммы (в тетрадке есть закомменченая ячейка с Phrases,  можно также попробовать другие способы построить нграммы); 

3) сделайте хороший словарь (отфильтруйте слишком частотные и редкие слова, попробуйте удалить стоп-слова); 

4) постройте несколько LDA моделей (переберите количество тем, можете поменять alpha, passes), если получаются плохие темы, поработайте дополнительно над предобработкой и словарем; 

5) для самой хорошей модели в отдельной ячейке напечатайте 3 хороших (на ваш вкус) темы;

6) между словарем и обучением модели добавьте tfidf (`tfidf = gensim.models.TfidfModel(corpus, id2word=dictionary); corpus = tfidf[corpus]`);

7) повторите пункт 4 на преобразованном корпусе (подбирайте параметры, ориентируясь на качество, а не на результаты, которые вы получали без tfidf);

8) в отдельной ячейке сравните лучшую модель без tfidf и лучшую модель с tfidf (приведите несколько тем, которые стали лучше или хуже, или которых раньше вообще не было; можно привести значения перплексии и когерентности для обеих моделей)

9) проделайте такие же действия для NMF (образец в конце тетрадки), для построения словаря воспользуйтесь возможностями Count или Tfidf Vectorizer (попробуйте другие значение max_features, min_df, max_df, сделайте нграмы через ngram_range, если хватает памяти), попробуйте такие же количества тем

10) в отдельной ячейки напечатайте темы лучшей NMF модели, сравните их с теми, что получились в LDA.

Сохраните тетрадку с экспериментами и положите её на гитхаб, ссылку на неё укажите в форме.

**Оцениваться будут главным образом пункты 5, 8 и 10. (2, 3, 2 баллов соответственно). Чтобы заработать остальные 3 балла, нужно хотя бы немного изменить мой код на промежуточных этапах (добавить что-то, указать другие параметры и т.д). **


Острожнее интерпретируйте полученные результаты. Если один алгоритм сработал хорошо в этом задании - не значит, что он всегда будет хорошо работать, и наоборот.